# gpCAM Test Notebook
In this notebook we will go through many features of gpCAM. Work through it 
and you are ready for your own autonomous experiment. 

## This first cell has nothing to do with gpCAM, it's just a function to plot some results later

In [37]:
import plotly.graph_objects as go
import numpy as np
def plot(x,y,z,data = None):
    fig = go.Figure()
    fig.add_trace(go.Surface(x = x, y = y,z=z))
    if data is not None: 
        fig.add_trace(go.Scatter3d(x=data[:,0], y=data[:,1], z=data[:,2],
                                   mode='markers'))

    fig.update_layout(title='Posterior Mean', autosize=True,
                  width=800, height=800,
                  margin=dict(l=65, r=50, b=65, t=90))


    fig.show()

## Here we want to define some points at which we will predict, still has nothing to do with gpCAM 

In [38]:
x_pred = np.zeros((10000,2))
x = np.linspace(0,10,100)
y = np.linspace(0,10,100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.array([x[i,j],y[i,j]])
        counter += 1

## Let's get after it by setting up a Single-Task GP Autonomous Data Acquisition Run

In [39]:
def optional_acq_func(x,obj):
    #this acquisition function makes the autonomous experiment a Bayesian optimization
    a = 3.0 #3.0 for 95 percent confidence interval
    mean = obj.posterior_mean(x)["f(x)"]
    cov = obj.posterior_covariance(x)["v(x)"]
    return mean + a * cov

def optional_cost_function(origin,x,arguments = None):
    #cost pf l1 motion in the input space
    offset = arguments["offset"]
    slope = arguments["slope"]
    d = np.abs(np.subtract(origin,x))
    c = (d * slope) + offset
    n = np.sum(c)
    return n
def optional_cost_update_function(costs, parameters):
    ###defining a cost update function might look tricky but just need a bit
    ###of tenacity. And remember, this is optional, if you have a great guess for your costs you
    ###don't need to update the costs. Also, if you don't account for costs, this funciton is not needed
    from scipy.optimize import differential_evolution as devo
    print("Cost adjustment in progress...")
    print("old cost parameters: ",parameters)
    bounds = np.array([[0.001,10],[0.0001,10]])
    ###remove outliers:
    origins = []
    points = []
    motions = []
    c   = []
    cost_per_motion = []
    for i in range(len(costs)):
        origins.append(costs[i][0])
        points.append(costs[i][1])
        motions.append(abs(costs[i][0] - costs[i][1]))
        c.append(costs[i][2])
        cost_per_motion.append(costs[i][2]/optional_cost_function(costs[i][0],costs[i][1], parameters))
    mean_costs_per_distance = np.mean(np.asarray(cost_per_motion))
    sd = np.std(np.asarray(cost_per_motion))
    for element in cost_per_motion:
        if (
            element >= mean_costs_per_distance - 2.0 * sd
            and element <= mean_costs_per_distance + 2.0 * sd
        ):
            continue
        else:
            motions.pop(cost_per_motion.index(element))
            c.pop(cost_per_motion.index(element))
            origins.pop(cost_per_motion.index(element))
            points.pop(cost_per_motion.index(element))
            cost_per_motion.pop(cost_per_motion.index(element))
    def compute_l1_cost_misfit(params, origins,points, costs):
        parameters = {"offset": params[0], "slope": params[1]}
        sum1 = 0.0
        for idx in range(len(points)):
            sum1 = sum1 + (
                (optional_cost_function(origins[idx],points[idx],parameters) - costs[idx]) ** 2)
        return sum1
    res = devo(compute_l1_cost_misfit, bounds, args = (origins, points,c), tol=1e-6, disp=True, maxiter=300, popsize=20,polish=False)
    arguments = {"offset": res["x"][0],"slope": res["x"][1:]}
    print("New cost parameters: ", arguments)
    return arguments

In [45]:
import time
from gpcam.autonomous_experimenter import AutonomousExperimenterGP

def instrument(data):
    for entry in data:
        entry["value"] = np.sin(np.linalg.norm(entry["position"]))
        #entry["cost"]  = [np.array([0,0]),entry["position"],np.sum(entry["position"])]
    return data
#initialization
#feel free to try different acquisition functions, e.g. optional_acq_func, "covariance", "shannon_ig"
#note how costs are defined in for the autonomous experimenter
my_ae = AutonomousExperimenterGP(np.array([[0,10],[0,10]]),instrument,
                                 np.ones((3)),np.array([[0.001,100],[0.001,100],[0.001,100]]),
                                 init_dataset_size= 20, 
                                 acq_func = "covariance", #optional_acq_func, 
                                 #cost_func = optional_cost_function, 
                                 #cost_update_func = optional_cost_update_function,
                                 cost_func_params={"offset": 5.0,"slope":10.0})


print("length of the dataset: ",len(my_ae.x))

#training
#my_ae.train_async() #train asynchronously
my_ae.train()       #or not
#print("Initial training submitted")
#for i in range(2): #this loop shows how hyperparameters are changing if they are trained asynchronously
#    time.sleep(2)
#     my_ae.update_hps()
#my_ae.train_async()
#my_ae.update_hps()

New data communicated via tell()
CAUTION: you have not provided data variances in fvGP,
they will be set to 1 percent of the data values!
GP successfully initiated
Costs successfully initialized
##################################################################################
Initialization successfully concluded
now train(...) or train_async(...), and then go(...)
##################################################################################
length of the dataset:  20
fvGP training started with  20  data points
fvGP hyperparameter tuning in progress. Old hyperparameters:  [1. 1. 1.]  with old log likelihood:  20.157855520145276
method:  global
fvGP is performing a global differential evolution algorithm to find the optimal hyperparameters.
maximum number of iterations:  20
termination tolerance:  1e-06
bounds:  [[1.e-03 1.e+02]
 [1.e-03 1.e+02]
 [1.e-03 1.e+02]]
differential_evolution step 1: f(x)= 20.6929
differential_evolution step 2: f(x)= 20.5384
differential_evolution step 3

## Let's see what our initial model looks like

In [46]:
f = my_ae.gp_optimizer.posterior_mean(x_pred)["f(x)"]
f_re = f.reshape(100,100)

plot(x,y,f_re, data = np.column_stack([my_ae.x,my_ae.y]))

## Let's run the autonomus loop to 100 points

In [47]:
help(my_ae.go)

Help on method go in module gpcam.autonomous_experimenter:

go(N=1000000000000000.0, breaking_error=1e-50, retrain_globally_at=[100, 400, 1000], retrain_locally_at=[20, 40, 60, 80, 100, 200, 400, 1000], retrain_async_at=[1000, 2000, 5000, 10000], retrain_callable_at=[], update_cost_func_at=[], acq_func_opt_setting=<function AutonomousExperimenterGP.<lambda> at 0x7f472fd94550>, training_opt_callable=None, training_opt_max_iter=20, training_opt_pop_size=10, training_opt_tol=1e-06, acq_func_opt_max_iter=20, acq_func_opt_pop_size=20, acq_func_opt_tol=1e-06, acq_func_opt_tol_adjust=[True, 0.1], number_of_suggested_measurements=1) method of gpcam.autonomous_experimenter.AutonomousExperimenterGP instance
    function to start the autonomous-data-acquisition loop
    optional parameters:
    -----------
        * N = 1e15 ... run N iterations
        * breaking_error = 1e-15 ... run until breaking_error is achieved
        * retrain_globally_at = [100,400,1000]
        * retrain_locally_at = [

In [48]:
#run the loop
my_ae.go(N = 100, 
            retrain_async_at=[],
            retrain_globally_at = [],
            retrain_locally_at = [],
            acq_func_opt_setting = lambda number: "global" if number % 2 == 0 else "local",
            training_opt_callable = None,
            training_opt_max_iter = 20,
            training_opt_pop_size = 10,
            training_opt_tol      = 1e-6,
            acq_func_opt_max_iter = 20,
            acq_func_opt_pop_size = 20,
            acq_func_opt_tol      = 1e-6,
            acq_func_opt_tol_adjust = [True,0.1])#,update_cost_func_at = [30])
print("length of the dataset is now: ", len(my_ae.x))
#and that runs the autonomous loop

Date and time:        2021-07-21_14_14_33



iteration:  20
Run Time:  0.0005548000335693359      seconds
Number of measurements:  20
hps:  [0.37500694 1.75493179 0.98982587]
ask() initiated with hyperparameters: [0.37500694 1.75493179 0.98982587]
optimization method:  global
bounds:  None
finding acquisition function maxima...
optimization method  global
tolerance:  1e-06
population size:  20
maximum number of iterations:  20
bounds: 
[[ 0 10]
 [ 0 10]]
cost function parameters:  {'offset': 5.0, 'slope': 10.0}
differential_evolution step 1: f(x)= -0.606888
differential_evolution step 2: f(x)= -0.606888
differential_evolution step 3: f(x)= -0.608256
differential_evolution step 4: f(x)= -0.609736
differential_evolution step 5: f(x)= -0.61044
differential_evolution step 6: f(x)= -0.61044
differential_evolution step 7: f(x)= -0.61044
differential_evolution step 8: f(x)= -0.61044
differential_evolution step 9: f(x)= -0.61044
differential_evolution step 10: f(x)= -0.610561
differential_evol

differential_evolution step 1: f(x)= -0.582253
differential_evolution step 2: f(x)= -0.582253
differential_evolution step 3: f(x)= -0.586657
The acquisition function optimization resulted in: 
     x:  [[5.03563752 9.86029051]]
  f(x):  [-0.58665724]
acquisition funciton optimization tolerance changed to:  0.05866572443703601
Next points to be requested: 
[[5.03563752 9.86029051]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.37500694 1.75493179 0.98982587]



iteration:  31
Run Time:  0.43828773498535156      seconds
Numbe

differential_evolution step 2: f(x)= -0.564
differential_evolution step 3: f(x)= -0.564589
The acquisition function optimization resulted in: 
     x:  [[0.24341389 5.10504503]]
  f(x):  [-0.5645892]
acquisition funciton optimization tolerance changed to:  0.05645892016520341
Next points to be requested: 
[[0.24341389 5.10504503]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.37500694 1.75493179 0.98982587]



iteration:  37
Run Time:  0.6333663463592529      seconds
Number of measurements:  37
hps:  [0.37500694 1.75493179 




iteration:  44
Run Time:  0.8458282947540283      seconds
Number of measurements:  44
hps:  [0.37500694 1.75493179 0.98982587]
ask() initiated with hyperparameters: [0.37500694 1.75493179 0.98982587]
optimization method:  global
bounds:  None
finding acquisition function maxima...
optimization method  global
tolerance:  0.052142136389673945
population size:  20
maximum number of iterations:  20
bounds: 
[[ 0 10]
 [ 0 10]]
cost function parameters:  {'offset': 5.0, 'slope': 10.0}
differential_evolution step 1: f(x)= -0.536592
differential_evolution step 2: f(x)= -0.539721
differential_evolution step 3: f(x)= -0.543816
differential_evolution step 4: f(x)= -0.543816
The acquisition function optimization resulted in: 
     x:  [[7.53769353 4.03193993]]
  f(x):  [-0.54381605]
acquisition funciton optimization tolerance changed to:  0.05438160549250856
Next points to be requested: 
[[7.53769353 4.03193993]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done

differential_evolution step 3: f(x)= -0.511451
differential_evolution step 4: f(x)= -0.511451
The acquisition function optimization resulted in: 
     x:  [[5.87218013 2.70418778]]
  f(x):  [-0.51145051]
acquisition funciton optimization tolerance changed to:  0.051145050698005894
Next points to be requested: 
[[5.87218013 2.70418778]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.37500694 1.75493179 0.98982587]



iteration:  55
Run Time:  1.266801118850708      seconds
Number of measurements:  55
hps:  [0.37500694 1.75493

...

differential_evolution step 1: f(x)= -0.493672
differential_evolution step 2: f(x)= -0.499721
differential_evolution step 3: f(x)= -0.508865
differential_evolution step 4: f(x)= -0.508865
differential_evolution step 5: f(x)= -0.508865
The acquisition function optimization resulted in: 
     x:  [[9.87643751 5.21019221]]
  f(x):  [-0.50886475]
acquisition funciton optimization tolerance changed to:  0.05088647547510812
Next points to be requested: 
[[9.87643751 5.21019221]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.37500

Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.37500694 1.75493179 0.98982587]



iteration:  75
Run Time:  2.095224380493164      seconds
Number of measurements:  75
hps:  [0.37500694 1.75493179 0.98982587]
ask() initiated with hyperparameters: [0.37500694 1.75493179 0.98982587]
optimization method:  local
bounds:  None
finding acquisition function maxima...
optimization method  local
tolerance:  0.04942094402631442
population size:  20
maximum number of iterations:  20
bounds: 
[[ 0 10]
 [ 0 10]]
cost function parameters: 

differential_evolution step 1: f(x)= -0.475431
differential_evolution step 2: f(x)= -0.475781
differential_evolution step 3: f(x)= -0.478429
The acquisition function optimization resulted in: 
     x:  [[1.88827417 1.85578255]]
  f(x):  [-0.4784295]
acquisition funciton optimization tolerance changed to:  0.04784294994113016
Next points to be requested: 
[[1.88827417 1.85578255]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.37500694 1.75493179 0.98982587]



iteration:  81
Run Time:  2.328465461730957      seconds
Number o

differential_evolution step 4: f(x)= -0.477871
differential_evolution step 5: f(x)= -0.477871
differential_evolution step 6: f(x)= -0.478779
The acquisition function optimization resulted in: 
     x:  [[5.05640566 1.33141375]]
  f(x):  [-0.47877867]
acquisition funciton optimization tolerance changed to:  0.04787786697835973
Next points to be requested: 
[[5.05640566 1.33141375]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.37500694 1.75493179 0.98982587]



iteration:  87
Run Time:  2.5605690479278564      seconds
Number

differential_evolution step 4: f(x)= -0.464942
differential_evolution step 5: f(x)= -0.464942
differential_evolution step 6: f(x)= -0.464942
differential_evolution step 7: f(x)= -0.464942
differential_evolution step 8: f(x)= -0.464942
The acquisition function optimization resulted in: 
     x:  [[8.06140345 0.90539586]]
  f(x):  [-0.46494197]
acquisition funciton optimization tolerance changed to:  0.046494197391147775
Next points to be requested: 
[[8.06140345 0.90539586]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.3750






## Now let's plot the posterior mean after the experiment has concluded

In [49]:
res = my_ae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f, data = np.column_stack([my_ae.x,my_ae.y]))

## Running a Multi-Task GP Autonomous Data Acquisition
This example uses 21 (!) dim robot data and 7 tasks, which you can all use or pick a subset of them

In [50]:
##prepare some data
import numpy as np
from scipy.interpolate import griddata
data = np.load("sarcos.npy")
print(data.shape)
x = data[:,0:21]
y = data[:,21:23]

(4449, 28)


In [51]:
from gpcam.autonomous_experimenter import AutonomousExperimenterFvGP


def instrument(data):
    for entry in data:
        entry["values"] = griddata(x,y,entry["position"],method = "nearest", fill_value = 0)[0]
        entry["value positions"] = np.array([[0],[1]])
    return data

input_s = np.array([np.array([np.min(x[:,i]),np.max(x[:,i])]) for i in range(len(x[0]))])
print("index set (input space) bounds:")
print(input_s)
print("hps bounds:")
hps_bounds = np.empty((22,2))
hps_bounds[:,0] = 0.0001
hps_bounds[:,1] = 100.0
hps_bounds[0] = np.array([0.0001, 10000])
print(hps_bounds)
print("shape of y: ")
print(y.shape)

my_fvae = AutonomousExperimenterFvGP(input_s,2,1,instrument,np.ones((22)),hps_bounds,
                                     init_dataset_size= 10)
my_fvae.train()
my_fvae.go(N = 100)

index set (input space) bounds:
[[ -0.842481   0.661032]
 [ -0.939933  -0.085018]
 [ -0.46773    0.359348]
 [  0.797788   2.239407]
 [ -0.242241   1.278097]
 [ -0.919895   0.369078]
 [ -0.296364   0.686928]
 [ -4.771399   4.488624]
 [ -1.634053   2.289369]
 [ -2.884804   2.558282]
 [ -4.196409   3.734968]
 [ -3.067483   2.380553]
 [ -2.433971   1.978575]
 [ -3.180643   2.568279]
 [-48.072386  48.872604]
 [-25.585054  25.225171]
 [-24.697862  26.106756]
 [-36.19139   71.176937]
 [-38.485967  35.804308]
 [-22.103174  17.84188 ]
 [-36.502723  30.806254]]
hps bounds:
[[1.e-04 1.e+04]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]]
shape of y: 
(4449, 2)
CAUTION: fvGP reports that you h

differential_evolution step 1: f(x)= -7.88467
The acquisition function optimization resulted in: 
     x:  [[  0.58418823  -0.15124016   0.13403729   1.82429118   0.55744317
    0.22387524  -0.08192141   2.43297746   0.14284497   1.62399859
   -0.30954082  -2.4432567    1.71376508  -0.62723487 -44.19066919
    7.97572381 -24.56116286  68.35419988  32.7271416    1.05257157
  -33.9629881 ]]
  f(x):  [-7.88467185]
acquisition funciton optimization tolerance changed to:  0.7884671848081911
Next points to be requested: 
[[  0.58418823  -0.15124016   0.13403729   1.82429118   0.55744317
    0.22387524  -0.08192141   2.43297746   0.14284497   1.62399859
   -0.30954082  -2.4432567    1.71376508  -0.62723487 -44.19066919
    7.97572381 -24.56116286  68.35419988  32.7271416    1.05257157
  -33.9629881 ]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++

differential_evolution step 1: f(x)= -7.52513
The acquisition function optimization resulted in: 
     x:  [[ 4.85186807e-01 -4.83586143e-01 -1.25355733e-01  2.10072693e+00
   3.54504084e-03 -6.37572181e-01 -2.90902631e-01  1.16098676e+00
   1.12514917e+00 -2.20075216e-01 -3.83989270e+00  7.70258226e-01
   9.08872991e-01 -3.15936889e+00 -4.74513768e+01  1.09173432e+01
   2.41909083e+01  6.18757302e+01 -3.22838177e+01 -1.73644643e+01
  -2.86092158e+01]]
  f(x):  [-7.52513258]
acquisition funciton optimization tolerance changed to:  0.7525132578915346
Next points to be requested: 
[[ 4.85186807e-01 -4.83586143e-01 -1.25355733e-01  2.10072693e+00
   3.54504084e-03 -6.37572181e-01 -2.90902631e-01  1.16098676e+00
   1.12514917e+00 -2.20075216e-01 -3.83989270e+00  7.70258226e-01
   9.08872991e-01 -3.15936889e+00 -4.74513768e+01  1.09173432e+01
   2.41909083e+01  6.18757302e+01 -3.22838177e+01 -1.73644643e+01
  -2.86092158e+01]]
Sending request to instrument ...
Data received
Checking if data

differential_evolution step 1: f(x)= -7.33373
The acquisition function optimization resulted in: 
     x:  [[  0.62011123  -0.19894334   0.10053339   1.9200893    0.52294234
   -0.52040616   0.24987726  -1.57990627   0.35762945  -0.22273975
   -0.22046013  -2.18152629   0.53400995  -1.32090985 -44.89260379
  -12.73964359  21.01887929 -27.78424015  32.77988763  -6.13070368
   20.21306246]]
  f(x):  [-7.33372711]
acquisition funciton optimization tolerance changed to:  0.733372711039535
Next points to be requested: 
[[  0.62011123  -0.19894334   0.10053339   1.9200893    0.52294234
   -0.52040616   0.24987726  -1.57990627   0.35762945  -0.22273975
   -0.22046013  -2.18152629   0.53400995  -1.32090985 -44.89260379
  -12.73964359  21.01887929 -27.78424015  32.77988763  -6.13070368
   20.21306246]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
+++++++++++

differential_evolution step 1: f(x)= -13.7261
The acquisition function optimization resulted in: 
     x:  [[-1.32628969e-01 -4.84914415e-01 -2.87238083e-01  1.46100438e+00
   4.05024748e-01  2.33366146e-01 -2.10948486e-01  3.98918486e+00
   2.55559536e-01 -1.67434028e+00  2.63858318e-02  1.79477238e-01
  -9.32904360e-01  1.81696858e+00 -4.21138549e+01 -2.40261704e+01
  -2.26762510e+01 -8.89933051e+00 -3.68810558e+01 -2.01444670e+01
   3.00802962e+01]]
  f(x):  [-13.72608555]
acquisition funciton optimization tolerance changed to:  1.3726085546681788
Next points to be requested: 
[[-1.32628969e-01 -4.84914415e-01 -2.87238083e-01  1.46100438e+00
   4.05024748e-01  2.33366146e-01 -2.10948486e-01  3.98918486e+00
   2.55559536e-01 -1.67434028e+00  2.63858318e-02  1.79477238e-01
  -9.32904360e-01  1.81696858e+00 -4.21138549e+01 -2.40261704e+01
  -2.26762510e+01 -8.89933051e+00 -3.68810558e+01 -2.01444670e+01
   3.00802962e+01]]
Sending request to instrument ...
Data received
Checking if dat

...

differential_evolution step 1: f(x)= -11.8667
The acquisition function optimization resulted in: 
     x:  [[-6.57014766e-01 -5.86119925e-01 -2.85005190e-01  1.23868617e+00
   3.59695604e-02 -7.53826564e-01 -1.52764628e-01 -3.30482229e+00
   8.15054749e-01  2.12212907e+00  1.44088219e+00 -1.87291504e+00
  -1.96332624e+00 -2.69949780e+00 -2.32234190e+01  2.33877865e+01
   2.51626838e+01  5.15566141e+01  3.56645116e+01  8.45008927e+00
  -3.78952578e+00]]
  f(x):  [-11.86671211]
acquisition funciton optimization tolerance changed to:  1.1866712109973134
Next points to be requested: 
[[-6.57014766e-01 -5.86119925e-01 -2.85005190e-01  1.23868617e+00
   3.59695604e-02 -7.53826564e-01 -1.52764628e-01 -3.30482229e+00
   8.15054749e-01  2.12212907e+00  1.44088219e+00 -1.87291504e+00
  -1.96332624e+00 -2.69949780e+00 -2.32234190e+01  2.33877865e+01
   2.51626838e+01  5.15566141e+01  3.56645116e+01  8.45008927e+00
  -3.78952578e+00]]
Sending request to instrument ...
Data received
Checking if dat

Run Time:  33.32826066017151      seconds
Number of measurements:  89
hps:  [235.43967005  85.63731643  56.28916434  44.50902261  66.71784897
  50.50534962  65.41941679  70.87616909  28.45183102  30.59552095
  67.7371477   82.13802654  41.83770398  22.44631301  33.12848852
  30.5260976   33.91890619  84.4466885   99.96359322  54.62145708
  96.93448912 100.        ]
ask() initiated with hyperparameters: [235.43967005  85.63731643  56.28916434  44.50902261  66.71784897
  50.50534962  65.41941679  70.87616909  28.45183102  30.59552095
  67.7371477   82.13802654  41.83770398  22.44631301  33.12848852
  30.5260976   33.91890619  84.4466885   99.96359322  54.62145708
  96.93448912 100.        ]
optimization method:  local
bounds:  None
finding acquisition function maxima...
optimization method  local
tolerance:  1.2024784776466062
population size:  20
maximum number of iterations:  20
bounds: 
[[ -0.842481   0.661032]
 [ -0.939933  -0.085018]
 [ -0.46773    0.359348]
 [  0.797788   2.239407]

  96.93448912 100.        ]
optimization method:  global
bounds:  None
finding acquisition function maxima...
optimization method  global
tolerance:  1.0313499133698538
population size:  20
maximum number of iterations:  20
bounds: 
[[ -0.842481   0.661032]
 [ -0.939933  -0.085018]
 [ -0.46773    0.359348]
 [  0.797788   2.239407]
 [ -0.242241   1.278097]
 [ -0.919895   0.369078]
 [ -0.296364   0.686928]
 [ -4.771399   4.488624]
 [ -1.634053   2.289369]
 [ -2.884804   2.558282]
 [ -4.196409   3.734968]
 [ -3.067483   2.380553]
 [ -2.433971   1.978575]
 [ -3.180643   2.568279]
 [-48.072386  48.872604]
 [-25.585054  25.225171]
 [-24.697862  26.106756]
 [-36.19139   71.176937]
 [-38.485967  35.804308]
 [-22.103174  17.84188 ]
 [-36.502723  30.806254]]
cost function parameters:  {}
differential_evolution step 1: f(x)= -12.2342
The acquisition function optimization resulted in: 
     x:  [[ 6.29751834e-02 -3.20339273e-01 -3.94104060e-02  1.40079553e+00
  -1.46949426e-02 -6.44934605e-01  5.2

acquisition funciton optimization tolerance changed to:  1.0337708138767219
Next points to be requested: 
[[ 3.20041781e-01 -4.16359394e-01 -3.84378571e-01  1.71907129e+00
   1.13991758e+00 -3.71024773e-01 -1.10482107e-01 -3.35481054e+00
   7.62003091e-03  1.53452769e-01  4.30185478e-01 -3.48766823e-01
   1.28090974e+00 -2.91029067e+00 -1.32964709e+01 -1.49494418e+01
  -2.36480341e+01  2.01312286e+01  1.20733963e+01 -1.12036962e+01
  -8.94438460e+00]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [235.43967005  85.63731643  56.28916434  44.50902261  66.71784897
  50.50534962

differential_evolution step 1: f(x)= -11.863
The acquisition function optimization resulted in: 
     x:  [[  0.15448057  -0.89967005   0.28853167   0.85946271   0.16057162
   -0.34984413  -0.26095506  -3.68639165   0.50393152  -0.69594462
   -2.73452444  -0.0777189    0.65490461   2.41982247  30.77783133
   24.87866897  17.81598575  69.55371974 -34.65355453  -3.9229774
  -32.52813638]]
  f(x):  [-11.86301576]
acquisition funciton optimization tolerance changed to:  1.186301575521662
Next points to be requested: 
[[  0.15448057  -0.89967005   0.28853167   0.85946271   0.16057162
   -0.34984413  -0.26095506  -3.68639165   0.50393152  -0.69594462
   -2.73452444  -0.0777189    0.65490461   2.41982247  30.77783133
   24.87866897  17.81598575  69.55371974 -34.65355453  -3.9229774
  -32.52813638]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
+++++++++++++

## Plotting the 0th task in a 2d slice

In [52]:
x_pred = np.zeros((10000,21))
x = np.linspace(input_s[0,0],input_s[0,1],100)
y = np.linspace(input_s[1,0],input_s[1,1],100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.zeros((21))
        x_pred[counter,[0,1]] = np.array([x[i,j],y[i,j]])
        counter += 1
res = my_fvae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f)

## Back to a single task: using the GPOptimizer class directly gives you some more flexibility
We will show more soon!

In [53]:
#/usr/bin/env python
import numpy as np
from gpcam.gp_optimizer import GPOptimizer

#initialize some data
x_data = np.random.uniform(size = (100,1))
y_data = np.sin(x_data)[:,0]


#initialize the GPOptimizer
my_gpo = GPOptimizer(1,np.array([[0,1]]))
#tell() it some data
my_gpo.tell(x_data,y_data)
#initialize a GP ...
my_gpo.init_gp(np.ones(2))
#and train it
my_gpo.train_gp(np.array([[0.001,100],[0.001,100]]))

#let's make a prediction
print(my_gpo.posterior_mean(np.array([0.44])))

#now we can ask for a new point
r = my_gpo.ask()
print(r)
#putting the ask() in a loop and updating the data will
#give you all you need for your autonomous experiment

New data communicated via tell()
CAUTION: you have not provided data variances in fvGP,
they will be set to 1 percent of the data values!
GP successfully initiated
fvGP training started with  100  data points
fvGP hyperparameter tuning in progress. Old hyperparameters:  [1. 1.]  with old log likelihood:  -95.61509504095825
method:  global
fvGP is performing a global differential evolution algorithm to find the optimal hyperparameters.
maximum number of iterations:  120
termination tolerance:  1e-06
bounds:  [[1.e-03 1.e+02]
 [1.e-03 1.e+02]]
differential_evolution step 1: f(x)= -156.313
differential_evolution step 2: f(x)= -156.313
differential_evolution step 3: f(x)= -156.541
differential_evolution step 4: f(x)= -156.569
differential_evolution step 5: f(x)= -156.569
differential_evolution step 6: f(x)= -156.758
differential_evolution step 7: f(x)= -156.894
differential_evolution step 8: f(x)= -156.957
differential_evolution step 9: f(x)= -157.079
differential_evolution step 10: f(x)= 